In [537]:
import json
import os
import time

import contextily as ctx
import geopandas as gpd
import numpy as np
import skmob
from mesa import Agent, Model
from mesa.batchrunner import BatchRunnerMP, BatchRunner
from mesa.datacollection import DataCollector
from mesa.time import RandomActivation, SimultaneousActivation
from tqdm import tqdm

# import nest_asyncio
# nest_asyncio.apply()

## Read distribution files

In [87]:
data_dir = '../../data/processed/mc/demography_abm/'
data_file = 'travel_prob_distr.json'
data_path = os.path.join(data_dir, data_file)

with open(data_path, 'r') as f:
  travel_distr = json.load(f)

In [88]:
data_file = 'regions_num_prob_distr.json'
data_path = os.path.join(data_dir, data_file)

with open(data_path, 'r') as f:
  regions_num_distr = json.load(f)

In [291]:
data_file = 'population_prob_distr.json'
data_path = os.path.join(data_dir, data_file)

with open(data_path, 'r') as f:
  population_distr = json.load(f)

In [90]:
data_file = 'demography_prob_distr.json'
data_path = os.path.join(data_dir, data_file)

with open(data_path, 'r') as f:
  demography_distr = json.load(f)

## Regions

In [525]:
kbr_data_path = '../../data/raw/KBR/'
kbr_dir_path = 'Etap_I_II_Wyznaczenie_obszaru_badan_liczby_mieszkancow_i_miejsc_pracy_na_podstawie_kart_SIM/Pliki_GIS_Wyznaczenie_obszaru_badan/2_Podzial_na_rejony/'
kbr_file_path = 'EtapII-REJONY_wroclaw.shp'

regions_file = os.path.join(kbr_data_path, kbr_dir_path, kbr_file_path)
regions = gpd.read_file(regions_file)
regions = regions.to_crs(epsg=3857)

## Neighboring regions for each region

In [499]:
region_neighbors = {}
for region in list(regions['NUMBER']):
    region_row = regions[regions['NUMBER'] == region].iloc[0]
    neighbors = regions[~regions.geometry.disjoint(region_row.geometry)]
    neighbors = neighbors['NUMBER'].to_list()
    region_neighbors[region] = neighbors

In [501]:
region_neighbors[12]

[24, 11, 12, 54, 55, 332, 336, 352]

## Mesa

In [619]:
class Person(Agent):
    """ An agent with -."""
    def __init__(self, unique_id, model):
        super().__init__(unique_id, model)
        demography_distr
        self.age_sex_comb = self._sample_agent_demography()
        self.start_region = self._sample_region()
        self.current_region = self.start_region
        self.end_region = self.start_region
        self.on_the_way = self._sample_status()

        if self.on_the_way:
            self.regions_num_left = self._sample_regions_num() - 1  # regions_num = 1 -> travel within the region
            self.regions_num = self.regions_num_left + 1
        else:
            self.regions_num_left = 0
            self.regions_num = self.regions_num_left

        self.travel_regions = []


    def _sample_agent_demography(self):
        sample = np.random.multinomial(1, list(demography_distr.values()))
        sample = np.argmax(sample)
        agent_sex_comb = list(demography_distr.keys())[sample]

        return agent_sex_comb


    def _sample_region(self):
        sample = np.random.multinomial(1, list(population_distr.values()))
        sample = np.argmax(sample)
        region = list(population_distr.keys())[sample]

        return region


    def _sample_status(self):
        try:
            sample = np.random.multinomial(1, list(travel_distr[self.age_sex_comb].values()))
        except KeyError:
            sample = [0, 1]  # agent_sex_comb = '0-5'
        status = not np.argmax(sample)

        return status


    def _sample_regions_num(self):
        try:
            sample = np.random.multinomial(1, list(regions_num_distr[self.age_sex_comb].values()))
        except KeyError:
            sample = np.random.multinomial(1, np.append([1], np.zeros(32)))
        regions_num = np.argmax(sample) + 1  # regions_num -> 1...33

        return regions_num


    # def _sample_next_region(self):
    #     sample = np.random.multinomial(1, list(neighbors_dist[str(self.current_region)].values()))
    #     sample = np.argmax(sample)
    #     next_region = int(list(neighbors_dist[str(self.current_region)].keys())[sample])

    #     return next_region


    def move_agent(self):
        # self.current_region = self._sample_next_region()
        # self.regions_num_left = self.regions_num_left - 1
        # -------------------------------------------------
        # current_region = regions[regions['NUMBER'] == int(self.current_region)].iloc[0]
        # neighbors = regions[~regions.geometry.disjoint(current_region.geometry)]
        # neighbors = neighbors['NUMBER'].to_list()
        neighbors = region_neighbors[int(self.current_region)]

        current_region = np.random.choice(neighbors)
        if not all(reg in self.travel_regions for reg in neighbors):
            while current_region in self.travel_regions:
                current_region = np.random.choice(neighbors)

        self.current_region = current_region
        self.travel_regions.append(self.current_region)
        self.regions_num_left = self.regions_num_left - 1


    def step(self):
        if self.on_the_way:
            self.move_agent()
            if self.regions_num_left == 0:
                self.on_the_way = False
                self.travel_regions = []
                self.end_region = self.current_region

In [620]:
class TrafficModel(Model):
    """A model with some number of agents."""
    def __init__(self, N):
        self.num_agents = N
        self.schedule = RandomActivation(self)
        self.running = True
        # Create agents
        for i in range(self.num_agents):
            agent = Person(i, self)
            self.schedule.add(agent)

        self.datacollector = DataCollector(
            agent_reporters={
                # "age_sex_comb": "age_sex_comb",
                "regions_num": "regions_num",
                "start_region": "start_region",
                "end_region": "end_region"
            }
        )


    def step(self):
        self.datacollector.collect(self)
        self.schedule.step()

In [558]:
model = TrafficModel(100000)  # 635701
for i in tqdm(range(34)):
    model.step()

100%|██████████| 34/34 [00:21<00:00,  1.55it/s]34 s



In [570]:
results = model.datacollector.get_agent_vars_dataframe().reset_index()
results = results[results["Step"] == 33]
#results = results[['age_sex_comb', 'start_region', 'end_region', 'AgentID']].groupby(['start_region', 'end_region']).count().reset_index()
results = results[['start_region', 'end_region', 'AgentID']].groupby(['start_region', 'end_region'])['AgentID'].count().reset_index(name='count')
results['start_region'] = results['start_region'].astype(int)
results['end_region'] = results['end_region'].astype(int)

In [621]:
print(f'Number of travels: {results.shape[0]}')

Number of travels: 22579


In [572]:
regions = regions.to_crs(epsg=4326)

In [573]:
fdf = skmob.FlowDataFrame(
    data=results,
    origin='start_region',
    destination='end_region',
    flow='count',
    tile_id='NUMBER',
    tessellation=regions
)

In [622]:
m = fdf.plot_tessellation(tiles='OpenStreetMap')
fdf.plot_flows(m, tiles='OpenStreetMap', min_flow=10, flow_weight=2)

In [623]:
fixed_params = {}
variable_params = {"N": [25000]}

batch_run = BatchRunner(
    TrafficModel,
    #nr_processes=4,
    variable_parameters=variable_params,
    fixed_parameters=fixed_params,
    iterations=28,
    max_steps=34,
    agent_reporters={
        # "age_sex_comb": "age_sex_comb",
        "regions_num": "regions_num",
        "start_region": "start_region",
        "end_region": "end_region"
    }
)

batch_run.run_all()

28it [04:22,  9.36s/it]262 s



In [624]:
results = batch_run.get_agent_vars_dataframe().reset_index()
#results = results[[start_region', 'end_region', 'AgentId']].groupby(['start_region', 'end_region']).count().reset_index()
results = results[['start_region', 'end_region', 'AgentId']].groupby(['start_region', 'end_region'])['AgentId'].count().reset_index(name='count')
results['start_region'] = results['start_region'].astype(int)
results['end_region'] = results['end_region'].astype(int)

In [625]:
print(f'Number of travels: {results.shape[0]}')

Number of travels: 46767


In [626]:
fdf = skmob.FlowDataFrame(
    data=results,
    origin='start_region',
    destination='end_region',
    flow='count',
    tile_id='NUMBER',
    tessellation=regions
)

In [632]:
m = fdf.plot_tessellation(tiles='OpenStreetMap')
fdf.plot_flows(m, tiles='OpenStreetMap', min_flow=75, flow_weight=2)

## Random stuff

In [427]:
travel_regions = []

In [436]:
current_region = regions[regions['NUMBER'] == 12].iloc[0]
neighbors = regions[~regions.geometry.disjoint(current_region.geometry)]
neighbors = neighbors['NUMBER'].to_list()
print(neighbors)

current_region = np.random.choice(neighbors)
print(current_region)

if not all(reg in travel_regions for reg in neighbors):
    while current_region in travel_regions:
        current_region = np.random.choice(neighbors)

travel_regions.append(current_region)

print(travel_regions)

[24, 11, 12, 54, 55, 332, 336, 352]
332
[332, 352, 24, 55, 336, 11, 12, 54, 332]
